In [1]:
import importlib

import argparse
import numpy as np
import pandas as pd
import sys

from pathlib import Path

from phppipy.ppi_tools import id_mapper
from phppipy.ppi_tools import ppi_import
from phppipy.ppi_tools import ppi_filter

In [10]:
input_dir = Path('/media/pieter/DATA/Wetenschap/Doctoraat/projects/host-pathogen-ppi-analysis/data/raw/ppi_data')
mitab_files = input_dir.glob('*.mitab')
ppi_df_list = [ppi_import.read_mi_tab(i) for i in mitab_files if i.is_file()]
phisto_files = input_dir.glob('phi*.csv')
mi_file = input_dir / 'mi.obo'
ppi_df_list.extend(
    [ppi_import.read_mitab_phisto(i, mi_file) for i in phisto_files])

Read PPI data set BIOGRID-ALL-3.4.160.mitab from /media/pieter/DATA/Wetenschap/Doctoraat/projects/host-pathogen-ppi-analysis/data/raw/ppi_data/BIOGRID-ALL-3.4.160.mitab
Read PPI data set hpidb2-19.02.2018.mitab from /media/pieter/DATA/Wetenschap/Doctoraat/projects/host-pathogen-ppi-analysis/data/raw/ppi_data/hpidb2-19.02.2018.mitab
Read PPI data set intact-virus-22.03.2018.mitab from /media/pieter/DATA/Wetenschap/Doctoraat/projects/host-pathogen-ppi-analysis/data/raw/ppi_data/intact-virus-22.03.2018.mitab
Read PPI data set virhostnet-01.2018.mitab from /media/pieter/DATA/Wetenschap/Doctoraat/projects/host-pathogen-ppi-analysis/data/raw/ppi_data/virhostnet-01.2018.mitab
Read PPI data set phi_data.csv from /media/pieter/DATA/Wetenschap/Doctoraat/projects/host-pathogen-ppi-analysis/data/raw/ppi_data/phi_data.csv


In [11]:
# Merge PPI datasets
for i in ppi_df_list:
    i['origin'] = i.name
ppi_df = pd.concat(ppi_df_list, axis=0, join='outer', ignore_index=True)

# remap to UniProt AC
id_mapper.check_unique_identifier(ppi_df)
out_mappings_dir = Path('/media/pieter/DATA/Wetenschap/Doctoraat/projects/host-pathogen-ppi-analysis/data/testdir3') / 'mapping'
full_mapping_file = Path('/media/pieter/DATA/Wetenschap/Doctoraat/projects/host-pathogen-ppi-analysis/data/idmappings-small.dat')

1715433 unique identifiers in column xref_A did not conform to the PSI-MITAB format (multiple identifiers were present) and a fix was attempted.

1715433 unique identifiers in column xref_B did not conform to the PSI-MITAB format (multiple identifiers were present) and a fix was attempted.



In [5]:
out_mappings_dir.mkdir(parents=True, exist_ok=True)
id_mapper.map2uniprot(ppi_df, out_mappings_dir, reviewed_only=True, local_run=True, full_mapping_file=full_mapping_file)





inside local mapper


FileNotFoundError: [Errno 2] No such file or directory: '/media/pieter/DATA/Wetenschap/Doctoraat/projects/host-pathogen-ppi-analysis/data/idmappings-small.dat'

In [15]:
ppi_df.loc[ppi_df.xref_A.str.contains('MULTMAP') | ppi_df.xref_B.str.contains('MULTMAP'),['xref_A', 'xref_B']]

Empty DataFrame
Columns: [xref_A, xref_B]
Index: []

In [39]:
mapping_dict = id_mapper._create_mapping_dict('/media/pieter/DATA/Wetenschap/Doctoraat/projects/host-pathogen-ppi-analysis/data/testdir3/mapping/entrez gene-locuslink2uniprot.txt', True)

In [40]:
mapping_dict

{'4961527': ['uniprotkb:Q9QR71'],
 '36288': ['uniprotkb:P32234'],
 '41720': ['uniprotkb:P81928'],
 '838837': ['uniprotkb:P48347'],
 '840380': ['uniprotkb:Q9S9Z8'],
 '839189': ['uniprotkb:Q9C5W6'],
 '826479': ['uniprotkb:P42643'],
 '178113': ['uniprotkb:P41932'],
 '542291': ['uniprotkb:P49106'],
 '844165': ['uniprotkb:Q01525'],
 '181348': ['uniprotkb:Q20655'],
 '833836': ['uniprotkb:P42644'],
 '4345634': ['uniprotkb:Q6ZKC0'],
 '840403': ['uniprotkb:P46077'],
 '831462': ['uniprotkb:P42645'],
 '830909': ['uniprotkb:P48349'],
 '543562': ['uniprotkb:P93211'],
 '821060': ['uniprotkb:Q96300'],
 '544213': ['uniprotkb:P93212'],
 '836668': ['uniprotkb:P48348'],
 '818859': ['uniprotkb:Q96299'],
 '419190': ['uniprotkb:Q5ZLQ6'],
 '7529': ['uniprotkb:P31946'],
 '54401': ['uniprotkb:Q9CQV8'],
 '56011': ['uniprotkb:P35213'],
 '547990': ['uniprotkb:Q96453'],
 '282125': ['uniprotkb:P62261'],
 '417554': ['uniprotkb:Q5ZMT0'],
 '42186': ['uniprotkb:P92177'],
 '7531': ['uniprotkb:P62258'],
 '22627': ['unipr

In [54]:
print('start')
def lambda_helper(row_entry, mapping_dict):
    # retrieve id mapping if it exists, otherwise retain original id
    original_id = row_entry.split(':')[1]
    new_id = mapping_dict.get(original_id, None)
    # if no list is returned by dict.get(), original id is passed
    if new_id:
        # if a new id is found in the mapping_dict, return it
        # mapping_dict contains lists, so extract or join for multiple mappings
        if len(new_id) > 1:
            print('multmap incoming!')
            new_id = 'MULT_MAP'.join(new_id)
        else:  # retrieve id as string from list
            new_id = new_id[0]
    else:
        # return original id if no remapping is found
        new_id = row_entry  # ROW ENTRY NOT original_id!!!
    print(new_id)
    return new_id

col='xref_B'
mapping_selection = ppi_df[col].str.startswith(
                    'entrez gene/locuslink:')
mapping_selection = ppi_df[col].str.contains(
                    '3105')
ppi_df.loc[mapping_selection, col].apply(func=lambda_helper, args=(mapping_dict,))
1

start
entrez gene/locuslink:31054
entrez gene/locuslink:31059
entrez gene/locuslink:31052
entrez gene/locuslink:33105
entrez gene/locuslink:31054
entrez gene/locuslink:31059
entrez gene/locuslink:43105
entrez gene/locuslink:33105
entrez gene/locuslink:43105
entrez gene/locuslink:43105
entrez gene/locuslink:31059
entrez gene/locuslink:31059
entrez gene/locuslink:43105
entrez gene/locuslink:31052
entrez gene/locuslink:173105
multmap incoming!
uniprotkb:P30443MULT_MAPuniprotkb:P04439
multmap incoming!
uniprotkb:P30443MULT_MAPuniprotkb:P04439
multmap incoming!
uniprotkb:P30443MULT_MAPuniprotkb:P04439
multmap incoming!
uniprotkb:P30443MULT_MAPuniprotkb:P04439
multmap incoming!
uniprotkb:P30443MULT_MAPuniprotkb:P04439
multmap incoming!
uniprotkb:P30443MULT_MAPuniprotkb:P04439
multmap incoming!
uniprotkb:P30443MULT_MAPuniprotkb:P04439
multmap incoming!
uniprotkb:P30443MULT_MAPuniprotkb:P04439
multmap incoming!
uniprotkb:P30443MULT_MAPuniprotkb:P04439
entrez gene/locuslink:31050
entrez gene/lo

1

In [53]:
mapping_selection = ppi_df[col].str.contains(
                    '3105')
ppi_df[mapping_selection]

aliases_A  \
1133     entrez gene/locuslink:DmelCG10324(gene name sy...   
1564     entrez gene/locuslink:CG11181(gene name synony...   
1842     entrez gene/locuslink:"BcDNA:AT06648"(gene nam...   
2654     entrez gene/locuslink:BP1018(gene name synonym...   
2811     entrez gene/locuslink:DmelCG14323(gene name sy...   
3962     entrez gene/locuslink:"BcDNA:GH06479"(gene nam...   
5351     entrez gene/locuslink:38C.34(gene name synonym...   
8371     entrez gene/locuslink:ARP(gene name synonym)|e...   
8961     entrez gene/locuslink:"BcDNA:GH03046"(gene nam...   
11548    entrez gene/locuslink:CG1467(gene name synonym...   
12932    entrez gene/locuslink:DmelCG16812(gene name sy...   
12981    entrez gene/locuslink:DmelCG1690(gene name syn...   
15069    entrez gene/locuslink:CG10439(gene name synony...   
20472    entrez gene/locuslink:CG 6811(gene name synony...   
25068    entrez gene/locuslink:CELE_T23H4.2(gene name s...   
130053   entrez gene/locuslink:DER-1(gene name synonym)...   
133093   entrez gene/locuslink:CD85J(gene name synonym)...   
154502   entrez gene/locuslink:CT1.4(gene name synonym)...   
157240   entrez gene/locuslink:CT1.1(gene name synonym)...   
162261   entrez gene/locuslink:CD158K(gene name synonym...   
163188   entrez gene/locuslink:IMD7(gene name synonym)|...   
163190   entrez gene/locuslink:TCRB(gene name synonym)|...   
171255   entrez gene/locuslink:NGS17(gene name synonym)...   
171259   entrez gene/locuslink:ABC17(gene name synonym)...   
300193   entrez gene/locuslink:CG13466(gene name synony...   
300943   entrez gene/locuslink:CG15010(gene name synony...   
325692   entrez gene/locuslink:AIB3(gene name synonym)|...   
326575   entrez gene/locuslink:Err2(gene name synonym)|...   
384514      entrez gene/locuslink:HMG20(gene name synonym)   
419329   entrez gene/locuslink:ATRGS1(gene name synonym...   
...                                                    ...   
1459625  entrez gene/locuslink:CG4082(gene name synonym...   
1459626  entrez gene/locuslink:CG4082(gene name synonym...   
1460549  entrez gene/locuslink:AKT(gene name synonym)|e...   
1461475  entrez gene/locuslink:CG10192(gene name synony...   
1462158  entrez gene/locuslink:CG14549(gene name synony...   
1463245  entrez gene/locuslink:BG5(gene name synonym)|e...   
1497953      entrez gene/locuslink:DLTS(gene name synonym)   
1498725  entrez gene/locuslink:CMD1GG(gene name synonym...   
1499540                                                  -   
1502887                                                  -   
1505196                                                  -   
1505890                                                  -   
1505923                                                  -   
1506315                                                  -   
1508778                                                  -   
1509425                                                  -   
1511138                                                  -   
1511985                                                  -   
1521309                                                  -   
1568079  psi-mi:q8tct4_human(display_long)|uniprotkb:PM...   
1568791  psi-mi:q9gzm7-1(display_long)|uniprotkb:PP6614...   
1568947  psi-mi:q9hbe1-1(display_long)|uniprotkb:PATZ1(...   
1613537  psi-mi:q9hbe1-1(display_long)|uniprotkb:PATZ1(...   
1613542  psi-mi:q8tct4_human(display_long)|uniprotkb:PM...   
1633587  psi-mi:ns1_i59a0(display_long)|uniprotkb:NS1A(...   
1633622  psi-mi:q2pjp0_9infa(display_long)|uniprotkb:NS...   
1649813                                uniprotkb:NS1_I59A0   
1672708                                                NaN   
1672713                                                NaN   
1672714                                                NaN   

                                                 aliases_B  \
1133     entrez gene/locuslink:CG3019(gene name synonym...   
1564     entrez gene/locuslink:CG11392(gene name synony...   
1842     entrez ge

In [59]:
with open('/media/pieter/DATA/Wetenschap/Doctoraat/projects/host-pathogen-ppi-analysis/data/interim/10292/mapping/refseq2uniprot.txt') as f:
    for line in f:
        print(line.split('\t'))

['yourlist:M20180531E29AEE828664DEEC55715D2BCC1634E10A53ACE', 'isomap:M20180531E29AEE828664DEEC55715D2BCC1634E10A53ACE', 'Entry', 'Entry name', 'Status', 'Protein names', 'Gene names', 'Organism', 'Length\n']
['NP_899152', 'NP_899152 -> Q9H074-3', 'Q9H074', 'PAIP1_HUMAN', 'reviewed', 'Polyadenylate-binding protein-interacting protein 1 (PABP-interacting protein 1) (PAIP-1) (Poly(A)-binding protein-interacting protein 1)', 'PAIP1', 'Homo sapiens (Human)', '479\n']
['NP_037450', 'NP_037450 -> Q5JSZ5-1', 'Q5JSZ5', 'PRC2B_HUMAN', 'reviewed', 'Protein PRRC2B (HLA-B-associated transcript 2-like 1) (Proline-rich coiled-coil protein 2B)', 'PRRC2B BAT2L BAT2L1 KIAA0515', 'Homo sapiens (Human)', '2229\n']
['NP_037450', '', 'Q9BU62', 'Q9BU62_HUMAN', 'unreviewed', 'BAT2L protein', 'BAT2L', 'Homo sapiens (Human)', '339\n']


In [61]:
with open('/media/pieter/DATA/Wetenschap/Doctoraat/projects/host-pathogen-ppi-analysis/data/interim/all/mapping/entrez gene-locuslink2uniprot.txt') as f:
    for line in f:
        print(line.split('\t'))

['36288', '', 'P32234', 'reviewed\n']
['41720', '', 'P81928', 'reviewed\n']
['41720', '', 'A0A0B4KFZ0', 'reviewed\n']
['838837', '', 'P48347', 'reviewed\n']
['838837', '', 'A0A178W0Z4', 'reviewed\n']
['838837', '', 'B9DFR1', 'reviewed\n']
['838837', '', 'F4I1C1', 'reviewed\n']
['840380', '', 'Q9S9Z8', 'reviewed\n']
['839189', '', 'Q9C5W6', 'reviewed\n']
['839189', '', 'A0A178WJF9', 'reviewed\n']
['826479', '', 'P42643', 'reviewed\n']
['826479', '', 'F4JJ94', 'reviewed\n']
['178113', '', 'P41932', 'reviewed\n']
['178113', '', 'N1NV25', 'reviewed\n']
['542291', '', 'P49106', 'reviewed\n']
['542291', '', 'B7ZYI0', 'reviewed\n']
['844165', '', 'Q01525', 'reviewed\n']
['181348', '', 'Q20655', 'reviewed\n']
['181348', '', 'Q95ZT1', 'reviewed\n']
['181348', '', 'W6E8Z9', 'reviewed\n']
['833836', '', 'P42644', 'reviewed\n']
['833836', '', 'A0A178UA42', 'reviewed\n']
['4345634', '', 'Q6ZKC0', 'reviewed\n']
['4345634', '', 'Q0J5J5', 'reviewed\n']
['840403', '', 'P46077', 'reviewed\n']
['840403',

['23357', '', 'A0A024R6B2', 'reviewed\n']
['90806', '', 'Q5VTE6', 'reviewed\n']
['90806', '', 'Q96AL9', 'reviewed\n']
['90806', '', 'B7Z297', 'reviewed\n']
['90806', '', 'B7Z5N3', 'reviewed\n']
['37748', '', 'Q24239', 'reviewed\n']
['283', '', 'P03950', 'reviewed\n']
['283', '', 'W0UV28', 'reviewed\n']
['23452', '', 'Q9UKU9', 'reviewed\n']
['23452', '', 'A0A024R868', 'reviewed\n']
['26360', '', 'Q9R045', 'reviewed\n']
['27329', '', 'Q9Y5C1', 'reviewed\n']
['51129', '', 'Q9BY76', 'reviewed\n']
['83854', '', 'Q8NI99', 'reviewed\n']
['83854', '', 'A0A024R7A9', 'reviewed\n']
['70726', '', 'Q8R0Z6', 'reviewed\n']
['10218', '', 'O43827', 'reviewed\n']
['55908', '', 'Q6UXH0', 'reviewed\n']
['284', '', 'Q15389', 'reviewed\n']
['284', '', 'B4DTQ9', 'reviewed\n']
['285', '', 'O15123', 'reviewed\n']
['51378', '', 'Q9Y264', 'reviewed\n']
['183', '', 'P01019', 'reviewed\n']
['183', '', 'B0ZBE2', 'reviewed\n']
['183', '', 'B2R5S1', 'reviewed\n']
['24179', '', 'P01015', 'reviewed\n']
['180291', '', '

['853139', '', 'P50080', 'reviewed\n']
['827891', '', 'O81906', 'reviewed\n']
['827891', '', 'A0A1P8B5P5', 'reviewed\n']
['827891', '', 'A0A178USE7', 'reviewed\n']
['3707654', '', 'P16913', 'reviewed\n']
['3707654', '', 'Q1PIL7', 'reviewed\n']
['598', '', 'Q07817', 'reviewed\n']
['598', '', 'Q5TE63', 'reviewed\n']
['598', '', 'A0A0S2Z3C5', 'reviewed\n']
['12048', '', 'Q64373', 'reviewed\n']
['12048', '', 'Q5HZH3', 'reviewed\n']
['12048', '', 'O35843', 'reviewed\n']
['24888', '', 'P53563', 'reviewed\n']
['24888', '', 'Q548R7', 'reviewed\n']
['24888', '', 'Q7TS62', 'reviewed\n']
['599', '', 'Q92843', 'reviewed\n']
['12050', '', 'P70345', 'reviewed\n']
['10017', '', 'Q9HD36', 'reviewed\n']
['10017', '', 'H0YMD5', 'reviewed\n']
['10018', '', 'O43521', 'reviewed\n']
['10018', '', 'A0A0C4DH20', 'reviewed\n']
['10018', '', 'A0A0A0MRE7', 'reviewed\n']
['12125', '', 'O54918', 'reviewed\n']
['12125', '', 'Q3U7X3', 'reviewed\n']
['12125', '', 'Q542N5', 'reviewed\n']
['12125', '', 'Q6PEB3', 'revie

['165055', '', 'Q96M89', 'reviewed\n']
['151278', '', 'Q96MF4', 'reviewed\n']
['285025', '', 'Q6ZP82', 'reviewed\n']
['285025', '', 'B8ZZB3', 'reviewed\n']
['57639', '', 'Q8IYE0', 'reviewed\n']
['57639', '', 'Q96MS1', 'reviewed\n']
['130940', '', 'Q8NFR7', 'reviewed\n']
['185121', '', 'Q93635', 'reviewed\n']
['91050', '', 'Q6ZUS6', 'reviewed\n']
['91050', '', 'A0A0U1RQD2', 'reviewed\n']
['8556', '', 'Q9UNH5', 'reviewed\n']
['8556', '', 'A0A0U1RQX7', 'reviewed\n']
['8556', '', 'Q59EF4', 'reviewed\n']
['8556', '', 'B4DY86', 'reviewed\n']
['8555', '', 'O60729', 'reviewed\n']
['284992', '', 'Q8NCX0', 'reviewed\n']
['284992', '', 'B8ZZI4', 'reviewed\n']
['284992', '', 'B4DZ03', 'reviewed\n']
['115948', '', 'A5D8V7', 'reviewed\n']
['115948', '', 'B3KPH7', 'reviewed\n']
['115948', '', 'K7EN59', 'reviewed\n']
['283152', '', 'Q494R4', 'reviewed\n']
['645811', '', 'A6NI56', 'reviewed\n']
['550631', '', 'Q569K6', 'reviewed\n']
['550631', '', 'A8MUK5', 'reviewed\n']
['126075', '', 'P0C7I6', 'revie

['319876', '', 'B1AZ15', 'reviewed\n']
['23242', '', 'O75128', 'reviewed\n']
['836213', '', 'Q94KT8', 'reviewed\n']
['836213', '', 'A0A178UFZ7', 'reviewed\n']
['836213', '', 'A0A1P8BCB5', 'reviewed\n']
['1303', '', 'Q99715', 'reviewed\n']
['395779', '', 'O42163', 'reviewed\n']
['395779', '', 'R9PXN6', 'reviewed\n']
['1690', '', 'O43405', 'reviewed\n']
['1879', '', 'Q9UH73', 'reviewed\n']
['1879', '', 'B4E2U8', 'reviewed\n']
['13591', '', 'Q07802', 'reviewed\n']
['13591', '', 'Q5SWK4', 'reviewed\n']
['13591', '', 'Q5SWK5', 'reviewed\n']
['13591', '', 'Q5SWK8', 'reviewed\n']
['13591', '', 'Q3UTW6', 'reviewed\n']
['13591', '', 'Q8CBL7', 'reviewed\n']
['116543', '', 'Q63398', 'reviewed\n']
['64641', '', 'Q9HAK2', 'reviewed\n']
['64641', '', 'B2RNT0', 'reviewed\n']
['64641', '', 'B7Z934', 'reviewed\n']
['253738', '', 'Q9H4W6', 'reviewed\n']
['13593', '', 'O08791', 'reviewed\n']
['13593', '', 'Q6NXL3', 'reviewed\n']
['13593', '', 'Q5DTH8', 'reviewed\n']
['57593', '', 'Q9BQW3', 'reviewed\n']


...

['41560', '', 'A0A0B4KFV7', 'reviewed\n']
['41560', '', 'A0A0B4KGX9', 'reviewed\n']
['41383', '', 'Q9VGM5', 'reviewed\n']
['40787', '', 'Q9VI16', 'reviewed\n']
['40787', '', 'A0A126GUQ4', 'reviewed\n']
['40787', '', 'Q0KIA8', 'reviewed\n']
['32501', '', 'Q9VXS4', 'reviewed\n']
['37933', '', 'Q9W139', 'reviewed\n']
['3346239', '', 'Q6NLM7', 'reviewed\n']
['40412', '', 'Q8MQZ8', 'reviewed\n']
['40412', '', 'Q9VNZ5', 'reviewed\n']
['40412', '', 'M9PIJ4', 'reviewed\n']
['35296', '', 'Q9VIP2', 'reviewed\n']
['39726', '', 'Q9VUU8', 'reviewed\n']
['42957', '', 'Q9XYZ6', 'reviewed\n']
['34123', '', 'Q9VLR2', 'reviewed\n']
['32924', '', 'Q7K0I7', 'reviewed\n']
['32924', '', 'Q9VWJ1', 'reviewed\n']
['39198', '', 'Q7YU08', 'reviewed\n']
['39198', '', 'M9ND74', 'reviewed\n']
['39198', '', 'M9PF74', 'reviewed\n']
['39198', '', 'A8JNQ4', 'reviewed\n']
['39198', '', 'Q9VT98', 'reviewed\n']
['39198', '', 'Q9VT99', 'reviewed\n']
['39198', '', 'A8JNQ5', 'reviewed\n']
['39198', '', 'M9NFQ7', 'reviewed\n'

['180896', '', 'Q17993', 'reviewed\n']
['176923', '', 'Q9N366', 'reviewed\n']
['175457', '', 'Q21453', 'reviewed\n']
['175457', '', 'Q5CZ47', 'reviewed\n']
['179324', '', 'Q8MNS8', 'reviewed\n']
['179324', '', 'H2KZK4', 'reviewed\n']
['172873', '', 'O62011', 'reviewed\n']
['172873', '', 'Q9U3S5', 'reviewed\n']
['175254', '', 'O01917', 'reviewed\n']
['174976', '', 'Q9NAG2', 'reviewed\n']
['172920', '', 'Q7K798', 'reviewed\n']
['172920', '', 'Q7K797', 'reviewed\n']
['172920', '', 'Q9U302', 'reviewed\n']
['172258', '', 'O44781', 'reviewed\n']
['178738', '', 'Q9N5G3', 'reviewed\n']
['187657', '', 'Q21799', 'reviewed\n']
['174926', '', 'O45441', 'reviewed\n']
['174926', '', 'O45440', 'reviewed\n']
['173952', '', 'H2KYU6', 'reviewed\n']
['173952', '', 'Q95QZ7', 'reviewed\n']
['172319', '', 'Q8IG69', 'reviewed\n']
['174323', '', 'A5JYR4', 'reviewed\n']
['174323', '', 'Q8I4G9', 'reviewed\n']
['174323', '', 'Q8I4H0', 'reviewed\n']
['174323', '', 'Q9U3A6', 'reviewed\n']
['183930', '', 'B3WFW0', 

['39148', '', 'M9PF54', 'reviewed\n']
['39148', '', 'M9PEZ7', 'reviewed\n']
['39012', '', 'Q9VSQ7', 'reviewed\n']
['42665', '', 'A8JR81', 'reviewed\n']
['42665', '', 'A8JR82', 'reviewed\n']
['42665', '', 'E2QD55', 'reviewed\n']
['42665', '', 'E2QD56', 'reviewed\n']
['42665', '', 'E1JIT7', 'reviewed\n']
['5740204', '', 'A8DQW8', 'reviewed\n']
['8674077', '', 'D2A6L8', 'reviewed\n']
['8674077', '', 'A0A0S0X2W5', 'reviewed\n']
['39462', '', 'Q9VU21', 'reviewed\n']
['32877', '', 'Q9VWP5', 'reviewed\n']
['32877', '', 'R9PY26', 'reviewed\n']
['41817', '', 'A0A0B4JDC8', 'reviewed\n']
['41817', '', 'Q9VFD3', 'reviewed\n']
['36496', '', 'A1Z9E0', 'reviewed\n']
['36496', '', 'A0A0B4K7Y4', 'reviewed\n']
['36496', '', 'A0A0B4KFL2', 'reviewed\n']
['36496', '', 'A1Z9D9', 'reviewed\n']
['42960', '', 'Q9VC31', 'reviewed\n']
['39448', '', 'Q9VU08', 'reviewed\n']
['32726', '', 'Q86B46', 'reviewed\n']
['32726', '', 'Q9VX51', 'reviewed\n']
['43314', '', 'Q9VB21', 'reviewed\n']
['59215', '', 'M9PFR8', 'rev

['832490', '', 'A0A178UBQ0', 'reviewed\n']
['817845', '', 'Q8GYK6', 'reviewed\n']
['817845', '', 'A0A178VY90', 'reviewed\n']
['817845', '', 'F4IUR2', 'reviewed\n']
['844387', '', 'Q9M8L6', 'reviewed\n']
['839798', '', 'Q9LP52', 'reviewed\n']
['839798', '', 'A0A178WN36', 'reviewed\n']
['821548', '', 'Q9LJZ2', 'reviewed\n']
['821548', '', 'F4JDH7', 'reviewed\n']
['821548', '', 'A0A178VCF0', 'reviewed\n']
['820782', '', 'Q9LDU3', 'reviewed\n']
['820782', '', 'A0A178VCE7', 'reviewed\n']
['818061', '', 'O64760', 'reviewed\n']
['821796', '', 'Q0V869', 'reviewed\n']
['821796', '', 'F4J076', 'reviewed\n']
['821796', '', 'A0A178VG73', 'reviewed\n']
['821796', '', 'A0A178VDZ2', 'reviewed\n']
['837519', '', 'Q941B2', 'reviewed\n']
['837519', '', 'A0A178W2B9', 'reviewed\n']
['838095', '', 'Q8H1F3', 'reviewed\n']
['838095', '', 'F4HZK3', 'reviewed\n']
['825014', '', 'Q84JS5', 'reviewed\n']
['825014', '', 'A0A178VCF6', 'reviewed\n']
['825014', '', 'F4J5V2', 'reviewed\n']
['820206', '', 'Q9CAE6', 're

['380928', '', 'A0T1J8', 'reviewed\n']
['380928', '', 'Q6ZQ32', 'reviewed\n']
['20402', '', 'R4GML0', 'reviewed\n']
['67341', '', 'M0QW46', 'reviewed\n']
['231051', '', 'F8WI37', 'reviewed\n']
['74041', '', 'E9QLR9', 'reviewed\n']
['228536', '', 'Z4YJL0', 'reviewed\n']
['258751', '', 'E9Q564', 'reviewed\n']
['269389', '', 'A2A473', 'reviewed\n']
['269389', '', 'E9Q0B9', 'reviewed\n']
['218397', '', 'E9PYG6', 'reviewed\n']
['245000', '', 'E9QPK4', 'reviewed\n']
['245000', '', 'A0A1L1SSL9', 'reviewed\n']
['17925', '', 'E9PWZ6', 'reviewed\n']
['17925', '', 'Q3TRQ0', 'reviewed\n']
['17925', '', 'E9PZW8', 'reviewed\n']
['17925', '', 'E9QKV6', 'reviewed\n']
['100126766', '', 'J3QN49', 'reviewed\n']
['72701', '', 'F8WIU3', 'reviewed\n']
['110521', '', 'F8VPM9', 'reviewed\n']
['12675', '', 'E9QNL4', 'reviewed\n']
['12675', '', 'Q3UDK0', 'reviewed\n']
['12675', '', 'Q3TPN9', 'reviewed\n']
['12675', '', 'Q8CBT3', 'reviewed\n']
['12675', '', 'E9Q605', 'reviewed\n']
['239673', '', 'Q8BIS2', 'revie

ensemblgenomes: 0 out of 0 identifiers were succesfully remapped to UniProt accession numbers.


In [35]:
import argparse
import numpy as np
import pandas as pd
import sys

from pathlib import Path

from phppipy.ppi_tools import id_mapper
from phppipy.ppi_tools import ppi_import
from phppipy.ppi_tools import ppi_filter
# input_dir = Path('/media/pieter/DATA/Wetenschap/Doctoraat/projects/host-pathogen-ppi-analysis/data/raw/ppi_data')
# mitab_files = input_dir.glob('*.mitab')
# ppi_df_list = [ppi_import.read_mi_tab(i) for i in mitab_files if i.is_file()]
# phisto_files = input_dir.glob('phi*.csv')
# mi_file = input_dir / 'mi.obo'
# ppi_df_list.extend(
#     [ppi_import.read_mitab_phisto(i, mi_file) for i in phisto_files])
# for i in ppi_df_list:
#     i['origin'] = i.name
# ppi_df = pd.concat(ppi_df_list, axis=0, join='outer', ignore_index=True)

ppi_file = Path('../data/interim/10292/ppi_data/10292-ppi-merged.tsv')
ppi_df = pd.read_csv(ppi_file, sep='\t', header=0)

# remap to UniProt AC
id_mapper.check_unique_identifier(ppi_df)

30332 unique identifiers in column xref_A did not conform to the PSI-MITAB format (multiple identifiers were present) and a fix was attempted.

30332 unique identifiers in column xref_B did not conform to the PSI-MITAB format (multiple identifiers were present) and a fix was attempted.



In [2]:
interaction_dataframe = ppi_df
col = 'xref_B'

In [3]:
mapping_selection = interaction_dataframe[col].str.startswith(
                    'ensemblgenomes')

In [4]:
mapping_dict = id_mapper._create_mapping_dict('/media/pieter/DATA/Wetenschap/Doctoraat/projects/host-pathogen-ppi-analysis/data/interim/10292-local5/mapping/ensemblgenomes2uniprot.txt', True)

In [5]:
mapping_dict

{'1965': ['uniprotkb:A0A0C7NQ84'],
 '2879': ['uniprotkb:A0A0C7NQU2'],
 '3659': ['uniprotkb:A0A0C7NUN3'],
 '3007': ['uniprotkb:A0A0C7NUP4'],
 '310': ['uniprotkb:A0A0C7N7L0'],
 '1398': ['uniprotkb:A0A0C7N5B3'],
 '327': ['uniprotkb:A0A0C7NR36'],
 '3015': ['uniprotkb:A0A0C7NBA4'],
 '3661': ['uniprotkb:A0A0C7NBA4'],
 '3665': ['uniprotkb:A0A0C7NEZ7'],
 '3664': ['uniprotkb:A0A0C7NUN9'],
 '1390': ['uniprotkb:A0A0C7NHJ4'],
 '293': ['uniprotkb:A0A0C7NIW6'],
 '2885': ['uniprotkb:A0A0C7N9A4'],
 '271': ['uniprotkb:A0A0C7NER3'],
 '1387': ['uniprotkb:A0A0C7NKL2'],
 '292': ['uniprotkb:A0A0C7NKM6'],
 '328': ['uniprotkb:A0A0C7NJV2'],
 '3326': ['uniprotkb:A0A0C7NAH6'],
 '2746': ['uniprotkb:A0A0C7NSJ3'],
 '1825': ['uniprotkb:A0A0C7N6E5'],
 '2590': ['uniprotkb:A0A0C7N849'],
 '3052': ['uniprotkb:A0A0C7NLL6'],
 '1355': ['uniprotkb:A0A0C7NHG2'],
 '2738': ['uniprotkb:A0A0C7N901'],
 '1351': ['uniprotkb:A0A0C7NNC4'],
 '3397': ['uniprotkb:A0A0C7NFT7'],
 '3066': ['uniprotkb:A0A0C7NF64'],
 '3054': ['uniprotkb:A0A0C

In [6]:
ppi_df.xref_B[mapping_selection]

Series([], Name: xref_B, dtype: object)

In [7]:
'YPL248C' in mapping_dict

False

In [36]:
columns=['xref_A','xref_B']
merged_columns = pd.unique(
        interaction_dataframe[columns].values.ravel('K'))
present_identifiers = id_mapper._extract_identifiers(merged_columns)

identifier_dict = {
    'ddbj/embl/genbank:': 'EMBL_ID',
    'ensembl:': 'ENSEMBL_ID',
    'ensemblgenomes:': 'ENSEMBLGENOME_ID',
    'entrez gene/locuslink:': 'P_ENTREZGENEID',
    'refseq:': 'P_REFSEQ_AC',
    'dip:': 'DIP_ID'
}

In [37]:
'ensemblgenomes:YPL248C' in merged_columns

False

In [38]:
ids = pd.Series(merged_columns)
ids = ids.str.split(':').str[1].unique()
ids = set(ids)

In [11]:
'YPL248C' in ids

False

P04386	EnsemblGenome	YPL248C
P04386	EnsemblGenome_TRS	YPL248C
P04386	EnsemblGenome_PRO	YPL248C



In [39]:
p = '/media/pieter/DATA/Wetenschap/Doctoraat/projects/host-pathogen-ppi-analysis/data/idmappingtest.dat'

In [13]:
id_mapper._create_mapping_files_local(merged_columns, p, '/media/pieter/DATA/Wetenschap/Doctoraat/projects/host-pathogen-ppi-analysis/data/testdir')

inside local mapper
No ddbj/embl/genbank: identifiers found in dataset.

No ensembl: identifiers found in dataset.

No ensemblgenomes: identifiers found in dataset.

No entrez gene/locuslink: identifiers found in dataset.

No refseq: identifiers found in dataset.

No dip: identifiers found in dataset.



In [14]:
mapping_dict = id_mapper._create_mapping_dict('/media/pieter/DATA/Wetenschap/Doctoraat/projects/host-pathogen-ppi-analysis/data/testdir/ensemblgenomes2uniprot.txt', True)

In [15]:
mapping_dict

{'YPL248C': ['uniprotkb:P04386']}

In [16]:
id_mapper.map2uniprot(ppi_df, '/media/pieter/DATA/Wetenschap/Doctoraat/projects/host-pathogen-ppi-analysis/data/testdir-map2',
                     local_run=True, full_mapping_file=p)


inside local mapper
No ddbj/embl/genbank: identifiers found in dataset.

No ensembl: identifiers found in dataset.

No ensemblgenomes: identifiers found in dataset.

No entrez gene/locuslink: identifiers found in dataset.

No refseq: identifiers found in dataset.

No dip: identifiers found in dataset.

outside
ensemblgenomes: 0 out of 0 identifiers were succesfully remapped to UniProt accession numbers.

entrez gene/locuslink: 0 out of 1111 identifiers were succesfully remapped to UniProt accession numbers.

0 identifiers were remapped to multiple UniProt accession numbers (denoted by the prefix "MULT_MAP" in the dataset) for a total of 0 interactions.



In [17]:
id_mapper._create_mapping_dict('/media/pieter/DATA/Wetenschap/Doctoraat/projects/host-pathogen-ppi-analysis/data/testdir-map2/ensemblgenomes2uniprot.txt', True)

{'YPL248C': ['uniprotkb:P04386']}

In [30]:
for db_tag, id_abbreviation in identifier_dict.items():
        # Define filepath (without forward slashes)
        path = Path('/media/pieter/DATA/Wetenschap/Doctoraat/projects/host-pathogen-ppi-analysis/data/testdir-map2') / (
            db_tag.replace('/', '-').strip(':') + r'2uniprot.txt')
        print(path)
        if Path(path).is_file():
            print('is file')
            mapping_dict = id_mapper._create_mapping_dict(path, True)
            print(mapping_dict)
            for col in columns:
                # note: use startswith to avoid mixing ensembl and embl ids...
                mapping_selection = interaction_dataframe[col].str.startswith(
                    db_tag)
                print(interaction_dataframe[mapping_selection].shape)
                mapping_selection = interaction_dataframe[col].str.startswith(
                    'ensemblgenomes')
                print(interaction_dataframe[mapping_selection].shape)

/media/pieter/DATA/Wetenschap/Doctoraat/projects/host-pathogen-ppi-analysis/data/testdir-map2/ddbj-embl-genbank2uniprot.txt
/media/pieter/DATA/Wetenschap/Doctoraat/projects/host-pathogen-ppi-analysis/data/testdir-map2/ensembl2uniprot.txt
/media/pieter/DATA/Wetenschap/Doctoraat/projects/host-pathogen-ppi-analysis/data/testdir-map2/ensemblgenomes2uniprot.txt
is file
{'YPL248C': ['uniprotkb:P04386']}
(0, 23)
(0, 23)
(0, 23)
(0, 23)
/media/pieter/DATA/Wetenschap/Doctoraat/projects/host-pathogen-ppi-analysis/data/testdir-map2/entrez gene-locuslink2uniprot.txt
is file
{'851572': ['uniprotkb:P13045'], '855828': ['uniprotkb:P04386']}
(2135, 23)
(0, 23)
(2135, 23)
(0, 23)
/media/pieter/DATA/Wetenschap/Doctoraat/projects/host-pathogen-ppi-analysis/data/testdir-map2/refseq2uniprot.txt
/media/pieter/DATA/Wetenschap/Doctoraat/projects/host-pathogen-ppi-analysis/data/testdir-map2/dip2uniprot.txt


{'YPL248C': ['uniprotkb:P04386']}

In [40]:
'ensemblgenomes:YPL248C' in merged_columns

False

In [41]:
'ensemblgenomes:YPL248C' in ids

False

In [42]:
ppi_df.loc[ppi_df['xref_A'].str.startswith('ensemblgenomes') | ppi_df['xref_B'].str.startswith('ensemblgenomes'), columns]

Empty DataFrame
Columns: [xref_A, xref_B]
Index: []

In [43]:
present_identifiers

['entrez gene/locuslink', 'refseq', 'intact']

In [44]:
ppi_df.loc[ppi_df['xref_A'].str.startswith('refseq') | ppi_df['xref_B'].str.startswith('refseq'), columns]

xref_A            xref_B
1428       uniprotkb:Q00403  refseq:NP_044650
1429       uniprotkb:Q00403  refseq:NP_044650
1439       uniprotkb:P14859  refseq:NP_044650
1440       uniprotkb:P14859  refseq:NP_044650
1455       uniprotkb:Q9Y4K3  refseq:NP_044625
1456       uniprotkb:Q9Y4K3  refseq:NP_044639
1457       uniprotkb:Q9Y4K3  refseq:NP_044639
1458       uniprotkb:Q9Y4K3  refseq:NP_044625
1463       uniprotkb:Q15750  refseq:NP_044639
1467       uniprotkb:Q9NYJ8  refseq:NP_044639
1535       uniprotkb:Q8VDD5  refseq:NP_044629
1536       uniprotkb:Q8VDD5  refseq:NP_044629
1537       uniprotkb:Q8VDD5  refseq:NP_044629
1538       uniprotkb:Q8VDD5  refseq:NP_044629
1592       uniprotkb:Q71SY5  refseq:NP_044650
1594       uniprotkb:Q71SY5  refseq:NP_044650
1597       uniprotkb:Q71SY5  refseq:NP_044650
1600       uniprotkb:Q71SY5  refseq:NP_044650
1601       uniprotkb:Q71SY5  refseq:NP_044650
1637       uniprotkb:P35579  refseq:NP_044629
1638       uniprotkb:P35579  refseq:NP_044629
1763       uniprotkb:P51617  refseq:NP_044639
1818       uniprotkb:Q16594  refseq:NP_044650
1907       uniprotkb:Q8VCD5  refseq:NP_044650
1909       uniprotkb:Q6PGF3  refseq:NP_044650
1942       refseq:NP_899152  uniprotkb:P89884
1944    refseq:XP_001723926  uniprotkb:P88989
1945    refseq:XP_001723926  uniprotkb:P88980
1949       refseq:NP_037450  uniprotkb:P88987
1960       uniprotkb:A2AGH6  refseq:NP_044650
...                     ...               ...
19767  uniprotkb:A0A1S5YGR5  refseq:YP_214113
19771  uniprotkb:A0A1S5YGR6  refseq:YP_214107
19775  uniprotkb:A0A1S5YGS0  refseq:YP_214095
19776  uniprotkb:A0A1S5YGS0  refseq:YP_214107
19777  uniprotkb:A0A1S5YGS0  refseq:YP_214108
19796  uniprotkb:A0A1S5YGT3  refseq:YP_214044
19797  uniprotkb:A0A1S5YGT3  refseq:YP_214113
19801  uniprotkb:A0A1S5YGX3  refseq:YP_214108
19806  uniprotkb:A0A1S5YGX5  refseq:YP_214044
19809  uniprotkb:A0A1S5YGY9  refseq:YP_214143
19810  uniprotkb:A0A1S5YGY9  refseq:YP_214143
19824  uniprotkb:A0A1S5YGZ4  refseq:YP_214108
19832  uniprotkb:A0A1S5YH00  refseq:YP_214113
19838  uniprotkb:A0A1S5YH01  refseq:YP_214057
19857  uniprotkb:A0A1S5YH07  refseq:YP_214044
19858  uniprotkb:A0A1S5YH07  refseq:YP_214107
19875  uniprotkb:A0A1S5YH17  refseq:YP_214113
19923      uniprotkb:D3XDR3  refseq:YP_214108
19935      uniprotkb:D3XDR4  refseq:YP_214108
19962      uniprotkb:D3XDT9  refseq:YP_214113
19987      uniprotkb:D3XDU0  refseq:YP_214113
20001      uniprotkb:D3XDY5  refseq:YP_214113
20237      uniprotkb:H2A1C7  refseq:YP_214057
20238      uniprotkb:H2A1C7  refseq:YP_214095
20239      uniprotkb:H2A1C7  refseq:YP_214108
20525      uniprotkb:H2A2G7  refseq:YP_214107
20600      uniprotkb:H2A2T4  refseq:YP_214113
20641      uniprotkb:H2A363  refseq:YP_214108
21917      uniprotkb:Q9H171  refseq:YP_214057
22185      uniprotkb:Q9Y572  refseq:YP_214057

[98 rows x 2 columns]